In [1]:
import requests
import pandas as pd
import seaborn as sns
import datetime
from pprint import pprint
import json
from tqdm.notebook import tqdm
from functools import reduce
import plotly.graph_objs as go
import plotly.express as px
from IPython.display import display, HTML
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)

### Data mapping

* C -> infecté
* D -> Décédé
* R -> Retabli
* V -> Doses injectee
* V2 -> Vaccins complete
* T -> Tests
* V(..) -> Variants
* I -> Soins intensifs
* H -> Hospitalisation

In [2]:
QUEBEC_DATA_URL = 'https://kustom.radio-canada.ca/covid-19/canada_quebec'


def get_region_df(region_data):
 
    resp = requests.get(region_data['Api'])
    data = json.dumps(resp.json()[0]['History'])  
    df = pd.read_json(data, convert_dates=['Date']).sort_values('Date')
    print(f"[{len(df)}] {region_data['Name']}")
    df['C_diff']= df['C'] - df['C'].shift(1)
    df['T_diff']= df['T'] - df['T'].shift(1)
    df['V_diff']= df['V'] - df['V'].shift(1)
    df['H_diff']= df['H'] - df['H'].shift(1)
    df['I_diff']= df['I'] - df['I'].shift(1)
    df['Region'] = region_data['Name']
    df['Population'] = int(region_data['Population'])
    return df

# Reads the Quebec data from the URL
resp = requests.get(QUEBEC_DATA_URL)
regions_raw_data = resp.json()[0]['Regions']

# for each region, fetch it and build a df
region_dfs = [get_region_df(region_data) for region_data in tqdm(regions_raw_data)]
df = pd.concat(region_dfs)

  0%|          | 0/18 [00:00<?, ?it/s]

[402] Montréal
[402] Montérégie
[402] Laval
[402] Capitale-Nationale
[402] Lanaudière
[402] Laurentides
[402] Mauricie - Centre-du-Québec
[402] Chaudière-Appalaches
[402] Estrie
[402] Saguenay–Lac-Saint-Jean
[402] Outaouais
[402] Bas-Saint-Laurent
[402] Gaspésie-Îles-de-la-Madeleine
[402] Abitibi-Témiscamingue
[402] Côte-Nord
[373] Eeyou Istchee
[402] Nord-du-Québec
[373] Nunavik


In [9]:
df['C_diff_per_capita'] = df['C_diff'] / df['Population'] * 100000
df['C_diff_per_capita_rolling'] = df['C_diff_per_capita'].rolling(3).mean()



fig = px.line(df,
              x='Date',
              y='C_diff_per_capita_rolling',
              color='Region' ,
              title='Cas par région'
)


fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
              annotation_text = 'last week', fillcolor='green', opacity=0.25, line_width=0)
fig.show()

In [4]:
df['V_diff_per_capita'] = df['V_diff'] / df['Population'] * 100000
df['V_diff_per_capita_rolling'] = df['V_diff_per_capita'].rolling(3).mean()

def trunc(string, l):
    if len(string) > l-5:
        return string[:l-5] + '(...)'
    return string

fig = px.line(df,
              x='Date',
              y='V_diff_per_capita_rolling',
              facet_col='Region',
              facet_col_wrap=6,
              facet_row_spacing=0.1,   
              facet_col_spacing=0.04,
              title='Vaccins Par Régions'
             
                    
)


fig.update_yaxes(matches=None, showticklabels=True, title='')
fig.update_xaxes(title='')
fig.for_each_annotation(lambda a: a.update(text=trunc(a.text, 20)))
fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
              fillcolor='green', opacity=0.25, line_width=0)

fig.show()

fig = px.line(df,
              x='Date',
              y='V_diff_per_capita_rolling',
              color='Region'                   
)


fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
              annotation_text = 'last week', fillcolor='green', opacity=0.25, line_width=0)
fig.show()


In [10]:
df['Semaine'] = df['Date'].dt.isocalendar().week

fig = px.scatter(df, y="C",x ='Date', color="Region",
                 #animation_frame='Semaine',
                title="", size='I')

fig.show()

In [78]:
#Taux de test
df['T_positivity'] = df['C_diff'] /  df['T_diff'] * 100
df['T_positivity_rolling'] = df['T_positivity'].rolling(7).mean()

#last 100 days
df2 = df[df['Date'] > pd.Timestamp(datetime.date.today() - datetime.timedelta(200))]

def trunc(string, l):
    if len(string) > l-5:
        return string[:l-5] + '(...)'
    return string

fig = px.line(df2,
              x='Date',
              y='T_positivity',
              facet_col='Region',
              facet_col_wrap=3,
              facet_row_spacing=0.03,   
              facet_col_spacing=0.04,
              height=1000,
              title='Taux de positivité')

fig.update_yaxes(showticklabels=True, title='')
fig.update_xaxes(title='')
fig.for_each_annotation(lambda a: a.update(text=trunc(a.text.split('=')[1], 40)))
fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
              fillcolor='green', opacity=0.25, line_width=0)

fig.show()


fig = px.line(df2,
              x='Date',
              y='T_positivity_rolling',
              color='Region'  ,
              title='Taux de positivite'
)


#fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
#              annotation_text = 'last week', fillcolor='green', opacity=0.25, line_width=0)
fig.show()



In [7]:
df['T_positivity'] = df['C_diff'] /  df['T_diff'] * 100
df2 = df[df['Date'] > pd.Timestamp(datetime.date.today() - datetime.timedelta(200))]
df3 = df2[df2['Region'] == "Outaouais" ]




from plotly.subplots import make_subplots
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=df3.Date, y=df3.T_positivity_rolling, name="positivity"),
    secondary_y=False,
)

fig.add_trace(
 go.Scatter(x=df3.Date, y=df3.T_diff_rolling, name="test_count"),
    secondary_y=True,
)

fig.show()


In [79]:
df['T_per_capita'] = df['T_diff'] / df['Population'] * 1000
df.loc[df.T_per_capita < 0, 'T_per_capita'] = 0
df['T_per_capita_rolling'] = df['T_per_capita'].rolling(7).mean()

#last 100 days
df2 = df[df['Date'] > pd.Timestamp(datetime.date.today() - datetime.timedelta(400))]



fig = px.line(df2,
              x='Date',
              y='T_per_capita',
              facet_col='Region',
              facet_col_wrap=3,
              facet_row_spacing=0.03,   
              facet_col_spacing=0.04,
              title='Tests Per capita',
              height=1200)
fig.update_yaxes(showticklabels=True, title='')
fig.update_xaxes(title='')
fig.for_each_annotation(lambda a: a.update(text=trunc(a.text.split('=')[1], 20)))
fig.add_vrect(x0=datetime.date.today(), x1=datetime.date.today() - datetime.timedelta(7),
              fillcolor='green', opacity=0.25, line_width=0)
fig.show()





In [68]:
df['T_per_capita'] = df['T_diff'] / df['Population'] * 100
df.loc[df.T_per_capita < 0, 'T_per_capita'] = 0
df2 = df[['Region', 'T_per_capita'] ].groupby(['Region']).sum().sort_values('T_per_capita').reset_index()

fig = px.bar(df2, x='Region', y='T_per_capita')
fig.show()